# Analyse aérodynamique d'une éolienne avec Xfoil
**Marc BUFFAT, département mécanique, UCB Lyon 1**
![eolienne](eolienne.jpg)

In [ ]:
%matplotlib inline
import sympy as sp
import numpy as np
import matplotlib.pyplot as plt
from validation.validation import check_function,bib_validation,exec_validation,info_etudiant
from validation.valide_markdown import test_markdown, test_code, test_algorithme
bib_validation('cours','MGC1061M')
#from Naca import Naca

## Xfoil

XFOIL est un programme pour la conception et l'analyse de profils isolés subsoniques développé au MIT dans les années 90 (https://web.mit.edu/drela/Public/web/xfoil/).

Il permet :
  1. une analyse visqueuse (ou non visqueuse) d'un profil aérodynamique existant avec prise en compte de 
         - transition forcée ou libre
         - séparation limitée du bord de fuite
         - correction de compressibilité de Karman-Tsien
         - nombres de Reynolds et/ou de Mach fixes ou variables
  2. un calcul potentiel (avec une méthode de singularité des panneaux) couplé à un calcul de couche limite 
     
Xfoil est écrit en Fortran 90 et on utilise une bibliothèque Python permettant de l'utiliser directement dans un programme Python.

### documentation originale

 [https://jupyterm1.mecanique.univ-lyon1.fr/cours_html/MGC1061M](/cours_html/MGC1061M)

In [ ]:
from xfoil import XFoil

### création d'une structure XFoil et définition du profil

In [ ]:
xf = XFoil()
naca_id = "23040"
xf.naca(naca_id)
naca = xf.airfoil

In [ ]:
def profil_plot(Xf,Yf,Label=None):
    """trace du profil naca"""
    if Label is not None:
        plt.plot(Xf,Yf,lw=2,label=Label)
        plt.plot([Xf[-1],Xf[0]],[Yf[-1],Yf[0]],lw=2)

    else:
        plt.plot(Xf,Yf,[Xf[-1],Xf[0]],[Yf[-1],Yf[0]],lw=2)
    plt.axis('equal')
    plt.axis('off')
    return

In [ ]:
plt.figure(figsize=(12,4))
profil_plot(naca.x,naca.y,naca_id)
plt.legend();

### définition des carcatéristiques d'un profil

- étude en fonction de l'angle $\alpha$ 
- on spécifie le nombre de Reynolds
- $C_L$ coefficiant de portance: projection suivant $\vec{N}=[-\sin\alpha, \cos\alpha]$ $\perp$ à $\vec{U}_0$

$$ C_L = \int_{C} Pr\, \vec{n}.\vec{N}\,ds $$

$$ C_L = \int_{C} Pr\, ds   \mbox{ avec } ds = dx \cos{\alpha} + dy \sin{\alpha} $$

- $C_m$ coefficient de moment (moment pression) par rapport à un point de référence $P=[x_{ref}=0.25, y_{ref}=0]$ , qui n'est donc pas nécessairement sur la ligne moyenne à 1/4 de corde

$$ C_m = \int_{C} Pr\, \vec{n} \land \vec{PM} \,ds $$

$$C_m =  \int_{C} -Pr \left((x-x_{ref}) dx + (y-y_{ref}) dy \right)$$

on calcul alors le moment en un point Q quelconque par la relation de transport

$$ \mathcal{M}_Q = \mathcal{M}_P + \vec{QP} \land \vec{F}_p  \mbox{ avec } \vec{F}_p = C_L [-\sin\alpha, \cos\alpha]$$

d'où la position du  centre de poussée exacte / à $P$  $x,y$ (erreur)

$$ \frac{C_m}{C_L} = (x- x_{ref})\cos\alpha + (y- y_{ref})\sin\alpha$$

### calcul avec xfoil 

toutes les quantités calculées sont adimensionnalisées par la dynamique de l'écoulement amont
$$q = \frac{1}{2} \rho U_0^2 $$. Donc un calcul sans dimension assume que le profil est tq $Lc=1$ (vria pour les profils NACA générés)

- Portance   $Cl = L/q$
- trainée    $Cd = D/q$
- moment par rapport au 1/4 corde (xp=0.25, yp=0)  $Cm = M/q$


calcul pour un angle alpha fixé (en degré)

      cl, cd, cm, cp = xf.a(angle)

distribution de pression

      xp,Pr = xf.get_cp_distribution()
      
nombre de Reynolds $Re=U_0/\nu$ = 0 

 - si calcul potentiel
      
      xf.Re = 0
      
 - si calcul avec CL xf.Re grand (calcul CL)

      xf.Re >> 1
      
      
affichage du calcul

      xf.print = True / False

In [ ]:
xf.Re = 1.e7
#xf.Re = 0
xf.print = True
cl, cd, cm, cp = xf.a(10)
print("resultat : ",cl,cd,cm,cd)

## Etude du profil  23020

In [ ]:
xf = XFoil()
naca_id = "23020"
xf.naca(naca_id)
naca = xf.airfoil
X,Y = naca.x, naca.y

## Analyse des caractéristiques aero

In [ ]:
# centre aerodynamique = 1/4 cordre / bord d'attaque
xp = 0.25
I=np.nonzero(np.abs(X-xp)<0.23e-2)[0]
yp = (Y[I].sum())/2.
print("centre aerodynamique :",I,xp,yp)

In [ ]:
plt.figure(figsize=(12,4))
profil_plot(X,Y,"23020")
plt.plot([xp],[yp],'o',label="centre de poussée")
plt.legend();

### portance, moment

In [ ]:
# analyse pour un angle fixe
Alpha=20
Cl, Cd, Cm, Cp = xf.a(Alpha)
print("Angle={} Lift={} Moment={} ".format(Alpha,Cl,Cm))
Xp,Pr = xf.get_cp_distribution()
plt.figure(figsize=(12,8))
plt.plot(Xp,Pr)
plt.title("pressure distribution")

In [ ]:
# centre de poussée
d = Cm/Cl
print("Position Centre de poussée:",d,xp,xp+d)

### translation du profil / centre aero 

In [ ]:
# translation du profil / au centre de poussé
print("centre de poussée :",xp,yp)
Xt = X - xp
Yt = Y - yp

In [ ]:
def trace_profil_rotation(X,Y,theta):
    """trace du profil avec une rotation de theta en degre"""
    ca = np.cos(theta*np.pi/180)
    sa = np.sin(theta*np.pi/180)
    X1 =  ca*X + sa*Y
    Y1 = -sa*X + ca*Y
    plt.plot(X1,Y1)
    plt.plot([0],[0],'o')
    plt.axis('equal')
    return

In [ ]:
trace_profil_rotation(Yt,Xt,40)
trace_profil_rotation(Yt,Xt,25)
trace_profil_rotation(Yt,Xt,0)

In [ ]:
# calcul portance fluide parfait pour # angles
alpha, cl, cd, cm, cp  = xf.aseq(0,25,1)

In [ ]:
from scipy import stats
a1,a0,r_v,r_p,err = stats.linregress(alpha,cl)
print("loi portance CL= {:.2f}*alpha + {:.2f}".format(a1,a0))

In [ ]:
plt.figure(figsize=(8,6))
plt.plot(alpha,cl,'o',label="C Lift")
plt.plot(alpha,a1*alpha+a0,'--')
plt.title("portance profil eclt potentiel")
plt.legend();

In [ ]:
# prise en compte de la viscosite
xf.Re = 1000000
alpha, cl, cd, cm, cp  = xf.aseq(0,25,1)

In [ ]:
# attention resultat
print(alpha)

In [ ]:
I = np.isfinite(alpha)
alpha = alpha[I]
cl = cl[I]
cd = cd[I]
cm = cm[I]

In [ ]:
plt.figure(figsize=(8,6))
plt.plot(alpha,cl,'o',label="C Lift")
plt.plot(alpha,cd,'-x',label="C drag")
plt.plot(alpha,a1*alpha+a0,'--',label="Potentiel")
plt.title("portance profil naca")
plt.legend();

### Choix du point de fonctionnement

valeur de l'angle $\alpha$

In [ ]:
plt.figure(figsize=(12,8))
plt.subplot(1,2,1)
plt.plot(cd,cl)
plt.title("polaire cl=f(cd)")
plt.subplot(1,2,2)
plt.plot(alpha,cl/cd)
plt.xlabel("$\\alpha$")
plt.title("finesse");

In [ ]:
# choix du point de fonctionnement alpha
ALPHA = 12
num=np.where(alpha==ALPHA)[0][0]
print(num,ALPHA)
CD = cd[num]
CL = cl[num]
print("pt fonctionnement ALPHA={} CL={} CD={}".format(ALPHA,CL,CD))

## Etude d'une pale d'eolienne

étude avec un profil **naca 23020**


![calage pale](calage_pale.png)


### caracteristique des pales
- puissance < 200kW
- longueur de L= 5 a 20 m 
- largeur max L/10
- rotation max de 400 a 100 tr/mn
- rotation omega ~ 20 tr/mn
- vrillage de la pale
- vitesse optimale du vent V0=15 m/s
- vitesse securité < 30 m/s
- vitesse minimale 4 m/s

Formule de Betz pour la puissance $P$:
  $$ P_{max} =  0.37 S V_0^3   \mbox{ avec } S= \pi L^2 $$
  
**Modélisation**
 - $\alpha$ angle d'attaque de la pale
 - $\beta$ angle de calage
 - $\phi$ angle de la vitesse apparente $V_a = V_0 - U$ 
 - $V_0$ vitesse vent
 - $U=\omega r$  vitesse de la pale en r 
 - direction tangentielle // à U
 - direction normale $\perp$
 - $L$ la portance est $\perp$ à $V_a$
 - $L_t$ projection tangentielle de cette force engendrant une rotation de la pale
 - $D$ trainée
 - $D_t$ projection tangentielle de cette force opposée à la rotation de la pale
 - $F_t = L_t -D_t$ résultante (utile) engendrant une puissance $F_t \omega r$


<img src="pale_eolienne1.png" style="display:inline-block;"> 
<img src="pale_eolienne2.png" style="display:inline-block;">

### Calcul du calage de l'éolienne: analyse dans le plan (t,z) 
- t: tangent et z: perpendiculaire au plan de l'éolienne 

on veut déterminer $\beta$ tq l'incidence $\alpha$ reste constante alors que U varie

In [ ]:
r, alpha, omega = sp.symbols('r alpha omega',positive=True)
U0,rho = sp.symbols('U_0 rho',positive=True)

In [ ]:
# longueur cordre (l0 en 0 et ~0 pour r = L)
L, l0 = sp.symbols('L l_0',positive=True)
lc = l0*(L-8*r/10)

In [ ]:
# angle de calage 
U = omega*r
phi = sp.atan2(U0,U)
beta = phi - alpha
beta

- angle de calage $\beta$ tq l'angle d'incidence $\alpha$ reste contant

In [ ]:
# vitesse apparente
Va = sp.sqrt(U0**2+U**2)
Va

In [ ]:
# portance et projection suivant la tangente (force utile)
Cp,Cd = sp.symbols('C_p C_d')
P  = Cp/2*rho*Va**2*lc
Pt = P*sp.cos(sp.pi/2-phi)
Pt = Pt.simplify()
display("Portance=",Pt)
# trainee
T = Cd*rho/2*Va**2*lc
Tt = -T*sp.cos(phi)
Tt = Tt.simplify()
display("Trainee ",Tt)

In [ ]:
# integration sur la pale pour avoir la force totale utile
FP = sp.integrate(Pt,(r,0,L)) + sp.integrate(Tt,(r,0,L)) 
FP = FP.simplify()
display("FP=",FP)

In [ ]:
# puissance totale
PP = sp.integrate(Pt*U,(r,0,L)) + sp.integrate(Tt*U,(r,0,L))
PP = PP.simplify()
display("Puissance totale=",PP)

## Valeurs numériques

In [ ]:
# Alpha angle d'incidence en degre, Omega vitesse rotation en tr/min
Alpha=ALPHA
Omega=40.
vals = {sp.pi:np.pi, l0: 1/15. , L:15. , alpha: Alpha*np.pi/180. , omega:Omega*2*np.pi/60., 
        U0:15., Cp:CL, Cd:CD, rho:1.0}
print(vals)
# formule Betz
Pmax = 0.37*(rho*sp.pi*L**2*U0**3).subs(vals)/1000
print("(Betz) Pmax={:.1f} kW".format(Pmax))

In [ ]:
display("Force totale:",FP)
print("Force portance:  {:.2f} N".format(FP.subs(vals)))
print("Puissance totale {:.2f} W".format(3*PP.subs(vals)))

In [ ]:
# estimation avec formule de Betz
Pmax = 0.37*rho*sp.pi*L**2*U0**3
print("Puissance Betz :",Pmax.subs(vals))

In [ ]:
Np = 20
R  = np.linspace(0.0,float(L.subs(vals)), Np)
PT = np.array([Pt.subs(vals).subs({r:rr}) for rr in R])
FT = PT + np.array([Tt.subs(vals).subs({r:rr}) for rr in R])
plt.plot(R,PT,label="Portance")
plt.plot(R,FT,label="Total")
plt.title("Force exercée sur la pale")
plt.xlabel("r")
plt.legend();

### calcul du calage sur 20 secteurs

In [ ]:
Np = 20
R  = np.linspace(0.0,float(L.subs(vals)), Np)
Lc = np.array([lc.subs(vals).subs({r:rr}) for rr in R])
plt.figure(figsize=(8,6))
plt.plot(R,Lc,lw=2)
plt.plot(R,np.zeros(R.size),lw=2)
plt.plot([0,0],[0,Lc[0]],lw=2)
plt.axis('equal')
plt.title("longueur corde eolienne");

In [ ]:
display("beta=",beta)
Beta = np.zeros(Np)
Beta[1:] = np.array([beta.subs(vals).subs({r:rr})*180./np.pi for rr in R[1:]])
Beta[0]  = 90. - Alpha
Beta

In [ ]:
plt.plot(R,Beta,label="$\\beta$")
plt.plot(R,Alpha*np.ones(Np),label="$\\alpha$")
plt.legend()

In [ ]:
# tracer des profils
plt.figure(figsize=(10,10))
for i in range(0,Np,2):
    #print(R[i],Beta[i],Lc[i])
    trace_profil_rotation(Yt*Lc[i],Xt*Lc[i],Beta[i])
plt.title("Calage de la pale")

In [ ]:
#from mpl_toolkits.mplot3d import Axes3D

def trace_profil3D(ax,X,Y,Z,theta,lw=2):
    ca = np.cos(theta*np.pi/180)
    sa = np.sin(theta*np.pi/180)
    X1 =  ca*X + sa*Y
    Y1 = -sa*X + ca*Y
    ax.plot(X1, Y1, Z)
    return

In [ ]:
fig = plt.figure(figsize=(10,10))
ax = fig.add_subplot(111, projection='3d')
#ax  = fig.gca(projection='3d')
for i in range(0,Np,1):
    #print(i,R[i])
    trace_profil3D(ax,Yt[::4]*Lc[i],Xt[::4]*Lc[i],R[i],Beta[i])
#ax.autoscale()
#ax.set_aspect('auto')
plt.axis('equal')
plt.grid()
plt.show()

# FIN